In [1]:
import csv, librosa, os
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import StandardScaler
import tensorflow as tf
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

path = "/home/bhm-ai/music_classification"
genres = 'blues classical country disco hiphop jazz metal pop reggae rock'.split()
songname = f'{path}/Data/genres_original/jazz/jazz.00029.wav'

num_mfcc = 20
n_fft = 2048
hop_length = 512

# header = 'filename chroma_stft spectral_centroid spectral_bandwidth rolloff zero_crossing_rate'
# header = 'filename chroma_stft_mean chroma_stft_var spectral_centroid_mean spectral_centroid_var spectral_bandwidth_mean spectral_bandwidth_var rolloff_mean rolloff_var zero_crossing_rate_mean zero_crossing_rate_var'
header = 'filename chroma_stft_mean chroma_stft_var rms_mean rms_var spectral_centroid_mean spectral_centroid_var spectral_bandwidth_mean spectral_bandwidth_var rolloff_mean rolloff_var zero_crossing_rate_mean zero_crossing_rate_var harmony_mean harmony_var perceptr_mean perceptr_var tempo'
for i in range(1, 21):
    header += f' mfcc{i}_mean mfcc{i}_var'
header += ' label'
header = header.split()

demo = True  
pre_dataset = True
epochs = 900 if not demo else 5
# epochs = 600 if not demo else 5

converter = LabelEncoder()

2024-06-19 09:19:56.870113: I external/local_tsl/tsl/cuda/cudart_stub.cc:32] Could not find cuda drivers on your machine, GPU will not be used.
2024-06-19 09:19:56.875426: I external/local_tsl/tsl/cuda/cudart_stub.cc:32] Could not find cuda drivers on your machine, GPU will not be used.
2024-06-19 09:19:56.926657: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-06-19 09:19:57.741657: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [2]:
# Training the model using the following parameters
# metrics = accuracy
# epochs = 600
# loss = sparse_categorical_crossentropy
# batch_size = 256
# optimizer = adam

def train_model(model,epochs,optimizer):
    batch_size=256
    model.compile(optimizer=optimizer,loss='sparse_categorical_crossentropy',metrics=['accuracy'])
    return model.fit(X_train,y_train,validation_data=(X_test,y_test),epochs=epochs,batch_size=batch_size)

def Validation_plot(history):
    print("Validation Accuracy",max(history.history["val_accuracy"]))
    pd.DataFrame(history.history).plot(figsize=(12,6))
    plt.show()

def readdata(df):
    df = df.drop(labels="filename",axis=1)
    
    fit = StandardScaler()
    X = fit.fit_transform(np.array(df.iloc[:,:-1],dtype=float))
    return X, df

# def extractfeature(y, sr, filename='_', g='_'):  # 60 columns; missing rms, harmony, perceptr, tempo

#     chroma_stft = librosa.feature.chroma_stft(y=y, sr=sr)
#     spec_cent = librosa.feature.spectral_centroid(y=y, sr=sr)
#     spec_bw = librosa.feature.spectral_bandwidth(y=y, sr=sr)
#     rolloff = librosa.feature.spectral_rolloff(y=y, sr=sr)
#     zcr = librosa.feature.zero_crossing_rate(y)
#     mfcc = librosa.feature.mfcc(y=y, sr=sr)
#     to_append = f'{filename} {np.mean(chroma_stft)} {np.var(chroma_stft)} {np.mean(spec_cent)} {np.var(spec_cent)} {np.mean(spec_bw)} {np.var(spec_bw)} {np.mean(rolloff)} {np.var(rolloff)} {np.mean(zcr)} {np.var(zcr)}'
#     for e in mfcc:
#         to_append += f' {np.mean(e)} {np.var(e)}'
#     to_append += f' {g}'
#     return to_append


def extractfeature(y, sr, filename='_', g='_'):
    chroma_hop_length = 512 #5000?
    chroma_stft = librosa.feature.chroma_stft(y=y, sr=sr, hop_length=chroma_hop_length)
    RMSEn= librosa.feature.rms(y=y)
    spec_cent = librosa.feature.spectral_centroid(y=y, sr=sr)
    spec_bw = librosa.feature.spectral_bandwidth(y=y, sr=sr)
    rolloff = librosa.feature.spectral_rolloff(y=y, sr=sr)
    zcr = librosa.feature.zero_crossing_rate(y)
    harmony, perceptr = librosa.effects.hpss(y=y)
    mfcc = librosa.feature.mfcc(y=y,sr=sr, n_mfcc=num_mfcc, n_fft=n_fft, hop_length=hop_length)
    mfcc = mfcc.T
    tempo, _ = librosa.beat.beat_track(y=y, sr = sr)
    to_append = f'{filename} {chroma_stft.mean()} {chroma_stft.var()} {RMSEn.mean()} {RMSEn.var()} {spec_cent.mean()} {spec_cent.var()} {spec_bw.mean()} {spec_bw.var()} {rolloff.mean()} {rolloff.var()} {zcr.mean()} {zcr.var()} {harmony.mean()} {harmony.var()} {perceptr.mean()} {perceptr.var()} {tempo}'
    for e in mfcc:
        to_append += f' {np.mean(e)} {np.var(e)}'
    # for x in range(20):
    #     to_append += f' {mfcc[:,x].mean()} {mfcc[:,x].var()}'
    to_append += f' {g}'
    return to_append


def extractfeature_(y, sr, filename='_', g='_'):  # 27 columns 
    chroma_stft = librosa.feature.chroma_stft(y=y, sr=sr)
    spec_cent = librosa.feature.spectral_centroid(y=y, sr=sr)
    spec_bw = librosa.feature.spectral_bandwidth(y=y, sr=sr)
    rolloff = librosa.feature.spectral_rolloff(y=y, sr=sr)
    zcr = librosa.feature.zero_crossing_rate(y)
    mfcc = librosa.feature.mfcc(y=y, sr=sr)
    to_append = f'{filename} {np.mean(chroma_stft)} {np.mean(spec_cent)} {np.mean(spec_bw)} {np.mean(rolloff)} {np.mean(zcr)}'    
    for e in mfcc:
        to_append += f' {np.mean(e)}'
    to_append += f' {g}'
    return to_append


def big_cnn_model(train=True):
    # https://www.tensorflow.org/api_docs/python/tf/keras/models/load_model
    if not train:
        model = tf.keras.models.load_model("model.keras")
    else:
        # We used different layers to train the neural network by importing keras library from tensorflow framework 
        # for input and hidden neurons we use the most widly used activation function which is relu where as for output neurons we uses softmax activation function
        model = tf.keras.models.Sequential([
            tf.keras.layers.Flatten(input_shape=(X.shape[1],)),
            tf.keras.layers.Dropout(0.2),
            
            tf.keras.layers.Dense(512,activation='relu'),
            tf.keras.layers.Dropout(0.2),
            
            tf.keras.layers.Dense(256,activation='relu'),
            tf.keras.layers.Dropout(0.2),
            
            tf.keras.layers.Dense(128,activation='relu'),
            tf.keras.layers.Dropout(0.2),
            
            tf.keras.layers.Dense(64,activation='relu'),
            tf.keras.layers.Dropout(0.2),
            
            tf.keras.layers.Dense(32,activation='relu'),
            tf.keras.layers.Dropout(0.2),
            
            tf.keras.layers.Dense(10,activation='softmax'),
        ])
        
        optimizer = tf.keras.optimizers.Adam(learning_rate=0.000146)
        model.compile(optimizer=optimizer,
                     loss="sparse_categorical_crossentropy",
                      metrics=["accuracy"])
        model.summary()
        model_history=train_model(model=model, epochs=epochs, optimizer='adam')
        
        test_loss,test_acc=model.evaluate(X_test,y_test,batch_size=256)
        print("The test loss is ",test_loss)
        print("The best accuracy is: ",test_acc*100)
        
        Validation_plot(model_history)
        model.save("model.keras")
    return model


def cnn_model(train=True):
    # https://www.tensorflow.org/api_docs/python/tf/keras/models/load_model
    if not train:
        model = tf.keras.models.load_model("model.keras")
    else:
        # We used different layers to train the neural network by importing keras library from tensorflow framework 
        # for input and hidden neurons we use the most widly used activation function which is relu where as for output neurons we uses softmax activation function
        model = tf.keras.models.Sequential()
        model.add(tf.keras.layers.Dense(256, activation='relu', input_shape=(X_train.shape[1],)))
        model.add(tf.keras.layers.Dense(128, activation='relu'))
        model.add(tf.keras.layers.Dense(64, activation='relu'))
        model.add(tf.keras.layers.Dense(10, activation='softmax'))
        
        optimizer = tf.keras.optimizers.Adam(learning_rate=0.000146)
        model.compile(optimizer=optimizer,
                     loss="sparse_categorical_crossentropy",
                      metrics=["accuracy"])
        model.summary()
        model_history=train_model(model=model, epochs=epochs, optimizer='adam')
        
        test_loss,test_acc=model.evaluate(X_test,y_test,batch_size=256)
        print("The test loss is ",test_loss)
        print("The best accuracy is: ",test_acc*100)
        
        Validation_plot(model_history)
        model.save("model.keras")
    return model

## tiền xử lí dữ liệu 

In [3]:
def predat_():
    return pd.read_csv(path + "/Data/features_3_sec.csv")

def predat():
    if pre_dataset:
        file = open(f'{path}/try_running__features_3_sec.csv', 'w', newline='')
        with file:
            writer = csv.writer(file)
            writer.writerow(header)
        genres = 'blues classical country disco hiphop jazz metal pop reggae rock'.split()
        for g in genres:
            ldir = list(os.listdir(f'{path}/Data/genres_original/{g}'))
            listfn = ldir[:5] if demo else ldir
            for filename in listfn:
                songname = f'{path}/Data/genres_original/{g}/{filename}'
                y, sr = librosa.load(songname, mono=True, duration=30)
                to_append = extractfeature(y, sr, filename, g)
                file = open(f'{path}/try_running__features_3_sec.csv', 'a', newline='')
                with file:
                    writer = csv.writer(file)
                    writer.writerow(to_append.split())
    return pd.read_csv(f"{path}/try_running__features_3_sec.csv")

df = predat()
df.head()

filename  \
blues.00076.wav 0.365587 0.087941 0.218970 0.004644 2645.530036 1.863852e+05 2426.005792 50776.462375  5611.974398 5.800167e+05 0.136469 0.002665 -1.128668e-02 0.035085 -0.006416 0.007281 [117.45383523]  5.910823 810.112793   6.648848 751.328186   6.009091 780.791077   6.900753 731.275146   7.101223 722.246887   6.682874 700.413696   6.353478 795.426392   4.919091 936.394043   4.844792 792.569580   7.653876 700.944031   8.081758 683.306763   8.169125 666.540710   7.992255 699.699890   7.933318 805.671448   7.990508 830.077820   8.012210 789.038635   7.352095 753.265625   5.261132 713.581665   1.986517 737.200623   0.597962 856.842651  -0.457416 972.833008  -1.229362 1110.523804 -2.148183 1202.535034 -1.009250 1183.656616  0.413889 938.233521   1.201195 794.779846   0.121046 740.133240  -0.435309  744.667358  -0.495536  789.056030   0.601366  877.312683   6.152036  875.538696   8.601122  697.003235    8.730181  574.834839    8.042827  583.429565   7.620489  727.091187   6.927419 956.855652   6.971634 1180.895874  7.051837 1328.154541  6.408492 1285.390625  4.672028 1265.398926  1.866080 1270.109863 -0.285018 1209.007080 -1.305966 1165.319092 -2.331856 1196.004150 -2.468345 1427.982056  4.403492 1473.330933  7.412259 1055.525024  6.367317 832.607422  4.630760 886.881470  3.520134 1283.042236 1.731537 1830.632568  3.664481 2123.063477  7.572631 1407.739746  9.926270 719.678345   10.094436 569.211304   9.417402 571.356995   8.323876 795.158569   7.428965 1047.634033  7.342669 1150.605103  6.808594 1171.875732  6.901929 1194.941162  6.986690 1166.779053  6.123765 1176.123779  6.633044 1268.563599  6.505502 1363.979126  6.287557 1406.129761  6.569949 1378.763428  6.916127  1210.923218  7.678607  1018.955933  7.771708  985.173462   7.052466  981.871765   6.572176 1140.625244  6.073725 1456.677002  5.914845 1740.715820  6.009864 811.822510   7.809642 602.153381   9.205317 557.727600   8.208872 576.705078   7.849950 702.977905   7.728155 828.999878   7.717472 917.190308   7.737119 930.405151   7.228044 888.606445   5.296756 930.901245   2.180964 922.926453  -0.142125 890.795105  -1.735344 909.386230  -0.856675 942.204407  -0.081764 950.632629  -0.609808 891.253784  -0.036973 747.182739  -0.377315 706.562439  -0.391602 677.858826  -1.358164 725.674744  -2.199206 837.716797  -2.646681 957.368347  -2.244850 952.689758   2.850214 814.639771   7.479371 673.890381   8.660391 585.286316   8.258420 589.799133   7.959090 737.407349   8.196643 822.566101   7.758806 881.348755   7.320305 925.484253   6.876664  947.113464   5.971399  977.365051   3.773132  1039.610718  1.343412  1186.806152  0.538791  1300.936768  2.118998  1152.086060  7.475703  882.791199   8.591311  754.744629   6.832649  701.040649   5.875178  759.777405   4.252732  892.111450   2.290423  1173.721436  1.367800  1633.364746  4.895690  1350.262939  9.129362  875.190735   10.587393 785.045959   9.321968  764.763123   7.763304  868.745422   5.936221 982.502625   5.216196 985.484985  4.786771 871.214844   4.621766 784.755371   3.864423 773.042053   3.115596 854.555786   2.997037 894.866394   3.746472 858.663391   3.946043 843.619141   4.043834 837.312866   3.945135 824.404785   4.050957 818.972473   3.751231 788.685974   3.265327 751.678162   3.756072 740.855103   4.312027 738.044800   4.711490  782.898560   5.136104  865.543457   3.595790  782.105286   3.464086  669.651978   6.365743  618.165894   6.753522  599.633789   6.031684 635.822571   4.995864 808.678833   4.468759 898.902649   4.851533 864.798950   5.299885 844.416626   5.558060 806.293518   5.584187 760.104553   3.943359 763.693542   0.963489 834.176270   0.218838 889.941772  -0.296512 778.957397  -0.284610 744.953247   0.420731 687.073608   2.037997  621.826660   2.235716  630.320190   1.335151 646.980286   0.131938 694.000427  -0.708741 776.400085   0.648968 825.770691   5.330164 701.397583   7.392898 616.455200   7.035250 585.804138   6.344514 592.931885   4.946723 784.036255   4.649035 883.698059   4.56528

In [4]:
print("Columns containing missing values",list(df.columns[df.isnull().any()]))

 # Label Encoding - encod the categorical classes with numerical integer values for training

# Blues - 0
# Classical - 1
# Country - 2
# Disco - 3
# Hip-hop - 4 
# Jazz - 5  
# Metal - 6 
# Pop - 7
# Reggae - 8
# Rock - 9
class_encod = df.iloc[:,-1]
Y = converter.fit_transform(class_encod)

X, df = readdata(df)
X_train,X_test,y_train,y_test=train_test_split(X, Y, test_size=0.3)

Columns containing missing values []


## CNN model

In [5]:
# model = cnn_model(True)  # cnn_model(False)
model = big_cnn_model(False)  # big_cnn_model(True)  # 

2024-06-19 09:21:32.683809: W tensorflow/core/common_runtime/gpu/gpu_device.cc:2251] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to use GPU. Follow the guide at https://www.tensorflow.org/install/gpu for how to download and setup the required libraries for your platform.
Skipping registering GPU devices...


trích xuất đặc trưng, lưu vào csv  # reference more at https://github.com/danyalimran93/Music-Emotion-Recognition/blob/master/Feature-Extraction.py

In [6]:
file = open('try_running__Extracted___Data.csv', 'w', newline='')
with file:
    writer = csv.writer(file)
    writer.writerow(header)

y, sr = librosa.load(songname, mono=True, duration=30

''

In [7]:
to_append = extractfeature(y, sr, filename='_', g='_')
len(to_append)

46865

In [8]:
file = open('try_running__Extracted___Data.csv', 'a', newline='')
with file:
    writer = csv.writer(file)
    writer.writerow(to_append.split())

df = pd.read_csv('try_running__Extracted___Data.csv')
df.head()

filename  \
_ 0.30434 0.091268 0.036304 0.000173 2235.344026 164848.722832 2259.025353 67328.900105 4683.438347 928652.527985 0.099404 0.00102 -0.000005 0.0007 -0.000048 0.000316 [112.34714674] -6.188691 5852.015625 -3.457526 4403.387695 -2.485886 3329.22583 -2.827668 2952.258057 -3.523114 3081.55957 -4.313613 3278.786377 -4.275342 3591.190674 -4.511599 3841.132812 -5.255757 4413.128906 -5.391147 4076.179199 -6.569302 3872.349121 -8.744378 4017.49292 -9.4408 3619.658936 -10.398784 3378.223145 -10.962314 3799.865723 -11.447293 4052.911621 -11.25897 3810.276123 -11.273236 3493.27002 -12.136221 3664.344971 -9.090935 3875.338623 -3.649588 3302.73291 -2.374307 3028.745605 -2.730966 3102.065918 -3.978958 3333.110107 -4.6217 3779.733154 -5.504045 3950.041016 -5.995328 3716.629395 -6.741102 3830.910156 -7.576272 3915.302246 -7.982895 3824.585449 -9.392522 3954.189453 -8.535672 4609.557617 -6.814177 4693.987305 -7.313463 4073.473145 -9.125001 3837.568848 -9.163839 3547.419189 -8.450815 3295.880371 -7.298998 2866.475098 -8.750676 3179.141113 -10.330778 3856.062988 -10.05358 4022.763184 -10.170115 3981.837402 -11.180753 4007.742188 -10.056355 4113.90625 -4.474731 3802.727295 -3.136855 3545.958496 -3.623878 3876.730957 -3.104568 4081.013672 -3.828482 3510.101562 -4.743398 3247.983643 -5.040618 3218.335693 -4.614596 3100.905762 -5.152764 3071.637207 -7.293882 3224.094238 -8.726757 3945.841797 -8.448745 3850.322266 -6.831334 3124.133545 -7.704243 2918.145264 -8.263037 3008.628906 -8.401081 3115.772705 -9.667253 2905.459717 -10.709564 2966.185059 -12.607553 3160.778809 -14.157133 3220.145996 -13.305519 3419.178467 -12.534937 3702.815918 -11.870885 3881.506348 -6.512725 3536.026123 -4.642715 3410.220703 -4.594774 3711.209717 -5.721602 3996.509277 -6.131342 4653.511719 -7.359624 4310.217773 -7.624294 3716.366455 -6.66589 3464.801514 -6.557274 3314.675781 -7.347111 3433.310547 -8.203609 3648.064453 -5.254393 4159.617188 -4.439935 4566.669922 -4.725711 3990.998535 -4.707656 3735.606689 -3.876366 3351.49292 -2.032988 2741.557617 -2.096422 2692.950684 -5.086012 2754.420166 -4.593536 2848.820312 -4.90347 2889.45166 -6.264836 2970.834229 -7.119195 3184.093018 -7.760025 3552.189453 -6.412665 3645.099609 -6.271816 3679.432129 -7.158404 3853.94873 -8.916159 3818.064941 -8.385222 3669.937988 -8.646876 3846.506592 -10.876395 4003.365967 -12.703436 3927.358643 -12.680655 3863.901123 -11.79698 4002.088379 -7.850236 3992.205078 -4.448855 3531.90625 -4.239938 2979.154297 -5.393732 2676.87915 -5.724324 2764.22998 -7.048122 2897.431152 -8.022455 2674.668457 -7.799742 2602.627197 -7.278397 2623.729248 -8.578798 2667.342285 -10.929741 2873.343262 -8.562277 2997.239746 -5.998243 2760.805908 -6.553202 2598.216309 -9.669291 2696.185059 -9.2048 2931.704346 -8.160711 2737.501953 -7.891448 2502.38916 -8.96117 2502.412842 -11.109365 2628.970947 -11.940321 2823.462646 -13.374067 3048.991699 -13.377591 3208.044678 -11.013028 3015.094238 -5.332684 2628.259277 -3.762043 2311.744629 -4.286656 2305.76416 -4.050268 2577.213623 -4.846585 2481.587402 -4.90607 2364.223145 -5.10299 2623.312012 -6.357558 3006.420654 -7.351565 3201.558105 -8.435888 3263.010986 -9.830423 3468.018311 -8.974484 3569.280518 -5.667926 3991.075439 -5.001977 4388.770996 -5.819898 4571.896973 -5.477988 4462.977539 -3.853626 3421.580566 -2.364235 2842.680908 -2.54953 2866.767334 -4.543913 3015.053223 -4.950059 3205.923584 -6.208614 3448.079346 -6.906009 3724.321045 -6.696401 3992.241455 -7.394306 4153.524902 -8.251923 4331.663086 -9.34712 4474.22168 -11.158308 4341.262695 -12.502994 4285.855469 -11.150949 3419.171143 -10.940058 3010.481201 -11.795985 3181.789551 -12.658285 3311.987549 -12.594404 3510.176514 -12.231108 3678.178955 -10.200167 3692.539551 -5.438654 3679.910645 -3.897316 3751.516846 -5.382184 4060.116455 -6.433139 4506.942383 -5.662614 3748.275879 -4.388864 2775.706543 -5.111576 2768.513184 -8.073496 3145.577637 -8.744922 3668.746826 -9.693465 4135.208008 -11.447525 4249.211914 -11.4158 4175.89

In [9]:
# # assert len(list(df.columns[df.isnull().any()])) > 0
X, df = readdata(df)
pred_x = model.predict(X)
pred_ind = np.argmax(pred_x, axis=1)
# print(labels[pred_ind])
print(converter.inverse_transform(pred_ind)[:1])
# print(pred_ind)
# print(class_encod)

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 64ms/step
['jazz']
